In [35]:
import pandas as pd
import numpy as np
import nltk
import contractions
import re
import gensim
from gensim.test.utils import datapath
from gensim import utils
from gensim.models import Word2Vec
import gensim.downloader
from gensim.test.utils import datapath
from gensim import utils
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Perceptron
from sklearn.svm import LinearSVC
from sklearn import metrics
from sklearn.metrics import accuracy_score

#### Importing the dataset

In [2]:
df= pd.read_table('amazon_reviews_us_Beauty_v1_00.tsv',on_bad_lines='skip',low_memory=False)

In [3]:
df.head(10)

marketplace  customer_id       review_id  product_id  product_parent  \
0          US      1797882  R3I2DHQBR577SS  B001ANOOOE         2102612   
1          US     18381298  R1QNE9NQFJC2Y4  B0016J22EQ       106393691   
2          US     19242472  R3LIDG2Q4LJBAO  B00HU6UQAG       375449471   
3          US     19551372  R3KSZHPAEVPEAL  B002HWS7RM       255651889   
4          US     14802407   RAI2OIG50KZ43  B00SM99KWU       116158747   
5          US      2909389  R1R30FA4RB5P54  B000NYL1Z6       166146615   
6          US     19397215  R30IJKCGJBGPJH  B001SYWTFG       111742328   
7          US      3195210  R18GLJJPVQ1OVH  B005F2EVMQ       255803087   
8          US     52216383   R8TVYIJXLYJT0  B00M1SUW7K       246816549   
9          US     10278216  R1CJGF6M3PVHEZ  B001KYQA1S         9612905   

                                       product_title product_category  \
0  The Naked Bee Vitmin C Moisturizing Sunscreen ...           Beauty   
1      Alba Botanica Sunless Tanning Lotion, 4 Ounce           Beauty   
2          Elysee Infusion Skin Therapy Elixir, 2oz.           Beauty   
3  Diane D722 Color, Perm And Conditioner Process...           Beauty   
4  Biore UV Aqua Rich Watery Essence SPF50+/PA+++...           Beauty   
5                          Murad Clarifying Cleanser           Beauty   
6  CoverGirl Queen Collection Perfect Point Plus ...           Beauty   
7           Bifesta Mandom Eye Makeup Remover, 145ml           Beauty   
8  Can You Handlebar All-Natural Secondary Mousta...           Beauty   
9  Maybelline Great Lash Washable Mascara, Clear ...           Beauty   

  star_rating  helpful_votes  total_votes vine verified_purchase  \
0           5            0.0          0.0    N                 Y   
1           5            0.0          0.0    N                 Y   
2           5            0.0          0.0    N                 Y   
3           5            0.0          0.0    N                 Y   
4           5            0.0          0.0    N                 Y   
5           4            0.0          0.0    N                 Y   
6           5            0.0          0.0    N                 Y   
7           5            0.0          0.0    N                 Y   
8           5            0.0          0.0    N                 Y   
9           1            0.0          2.0    N                 Y   

                                     review_headline  \
0                                         Five Stars   
1                          Thank you Alba Bontanica!   
2                                         Five Stars   
3                                         GOOD DEAL!   
4  this soaks in quick and provides a nice base f...   
5                                         Four Stars   
6                                           Good buy   
7                                         Five Stars   
8                             Tame the wild mustache   
9        but it's like having nothing on them at all   

                                         review_body review_date  
0                   Love this, excellent sun block!!  2015-08-31  
1  The great thing about this cream is that it do...  2015-08-31  
2  Great Product, I'm 65 years old and this is al...  2015-08-31  
3  I use them as shower caps & conditioning caps....  2015-08-31  
4  This is my go-to daily sunblock. It leaves no ...  2015-08-31  
5                                               Good  2015-08-31  
6  Great eyeliner, does run just a little bit at ...  2015-08-31  
7                               Best makeup remover！  2015-08-31  
8  This is a great product. I'm on my latest stab...  2015-08-31  
9  I thought it would darken the lashes even thou...  2015-08-31

In [4]:
df_fnl=df[['review_body','star_rating']]

#### Replacing the ratings and creating three classes

In [5]:
df_final=df_fnl.replace({'star_rating':{2:1,3:2,4:3,5:3,'5':3,'2':1,'3':2,'4':3,'1':1}})


In [6]:
df_final.isnull().sum()

review_body    400
star_rating     10
dtype: int64

In [7]:
df_final.dropna(inplace=True)

In [8]:
s0 = df_final[df_final['star_rating'].eq(1)].sample(20000).index
s1 = df_final[df_final['star_rating'].eq(2)].sample(20000).index 
s2 = df_final[df_final['star_rating'].eq(3)].sample(20000).index 

df_fi = df_final.loc[s0.union(s1).union(s2)]

In [9]:
df_fi['star_rating'].value_counts()

1    20000
3    20000
2    20000
Name: star_rating, dtype: int64

#### Applying the datacleaning techniques to lower, remove white spaces between words, contractions and HTMl and URL Tags

In [10]:
def remove_alphanumeric(s):
    s=s.lower()
    s=s.strip()
    s=contractions.fix(s)
    s=s.replace(r'<[^<>]*>', '')
    s=s.replace(r'http\S+', '').replace(r'www\S+', '')
    s=re.sub(r'[^a-zA-Z]',' ',s)
    return re.sub(' +', ' ',s)

In [11]:
df_fi['review_body']=df_fi['review_body'].apply(remove_alphanumeric)

In [12]:
df_fi

review_body star_rating
9        i thought it would darken the lashes even thou...           1
329                                             very well            3
409      i am disappointed that you have to wash it off...           2
447      this cream absorbs quickly into the skin is no...           2
514      the packaging has changed and not for the bett...           2
...                                                    ...         ...
5093988  i used this product on my face once leaving it...           1
5094149  i do not know why they bothered putting a quot...           1
5094265  although the electric razor gave a decent shav...           1
5094284  ladies if ever you have been distracted by uns...           2
5094303  like most sound machines the sounds choices ar...           2

[60000 rows x 2 columns]

### Word Embedding 

Part a

In [13]:
google_wrd2vc = gensim.downloader.load('word2vec-google-news-300')

In [14]:
print(google_wrd2vc.most_similar(positive=['woman', 'king'], negative=['man']))

[('queen', 0.7118193507194519), ('monarch', 0.6189674735069275), ('princess', 0.5902431011199951), ('crown_prince', 0.5499460697174072), ('prince', 0.5377321243286133), ('kings', 0.5236844420433044), ('Queen_Consort', 0.5235945582389832), ('queens', 0.518113374710083), ('sultan', 0.5098593831062317), ('monarchy', 0.5087411999702454)]


In [20]:
google_wrd2vc.similarity('good','better')

0.61207294

In [25]:
google_wrd2vc.similarity('machine','sounds')

0.16873193

In [29]:
print(google_wrd2vc.most_similar(positive=['king', 'woman'], negative=['man'], topn=1))

[('queen', 0.7118193507194519)]


Part b

In [15]:

class MyCorpus:
    ## step to create custom Corpus for Word2vec to use to generate word vectors
    def __iter__(self):
        for line in df_fi['review_body']:
            # assume there's one document per line, tokens separated by whitespace
            yield utils.simple_preprocess(line)

In [16]:
#Loading my own Word2Vec 
my_model= Word2Vec(sentences = MyCorpus(), vector_size = 300, window = 13, min_count = 9)

In [26]:
my_model.wv.similarity('machine','sounds')

0.275665

In [28]:
my_model.wv.similarity('good','better')

0.38031834

In [33]:
print(my_model.wv.most_similar(positive=['king', 'woman'], negative=['man'],topn=1))

[('depressed', 0.6841756701469421)]


The performance of the Pre-trained model by word2vec-google-news-300 is better since it has a much bigger corpus than my personal dataset. Therefore the pretrained mmodel can findout better similarities than my model.

#### Simple models

In [36]:
#Splitting data into train and test dataset

true_label = df_fi['star_rating'].to_numpy()
X_train, X_test, Y_train, Y_test = train_test_split(df_fi['review_body'], true_label, test_size=0.2, random_state=42)

In [41]:
##average Word2Vec vectors for each review as the input feature 

for row in df_fi['review_body']:
    sent_split=row.split(' ')
    for word in sent_split:
        if word in google_wrd2vc:
            
        
        
    

['i', 'thought', 'it', 'would', 'darken', 'the', 'lashes', 'even', 'though', 'it', 'is', 'clear', 'but', 'it', 'is', 'like', 'having', 'nothing', 'on', 'them', 'at', 'all', 'sadly', 'i', 'threw', 'it', 'away', '']
['very', 'well', '']
['i', 'am', 'disappointed', 'that', 'you', 'have', 'to', 'wash', 'it', 'off', 'before', 'you', 'add', 'your', 'nail', 'polish', 'seems', 'counterintuitive', 'to', 'wash', 'away', 'the', 'moisturizer', 'that', 'you', 'need', 'to', 'have', 'on', 'your', 'nails', '']
['this', 'cream', 'absorbs', 'quickly', 'into', 'the', 'skin', 'is', 'non', 'greasy', 'light', 'in', 'texture', 'aloe', 'vera', 'does', 'great', 'things', 'at', 'different', 'times', 'for', 'skin', 'but', 'has', 'not', 'done', 'much', 'as', 'a', 'softening', 'agent', 'for', 'my', 'feet', 'maybe', 'this', 'cream', 'is', 'good', 'for', 'burning', 'feet', '']
['the', 'packaging', 'has', 'changed', 'and', 'not', 'for', 'the', 'better', 'a', 'plastic', 'bag', 'replaced', 'the', 'cylinder', 'applicato

['i', 'am', 'not', 'a', 'fan', 'of', 'the', 'fact', 'that', 'i', 'still', 'get', 'acne', 'in', 'my', 'mid', 's', 'and', 'try', 'to', 'do', 'whatever', 'i', 'can', 'to', 'prevent', 'it', 'this', 'blemish', 'control', 'moisturizer', 'from', 'retseliney', 'has', 'been', 'a', 'great', 'way', 'to', 'control', 'my', 'breakouts', 'and', 'keep', 'my', 'face', 'hydrated', 'br', 'br', 'i', 'love', 'using', 'natural', 'ingredients', 'on', 'my', 'skin', 'and', 'the', 'benefits', 'this', 'moisturizer', 'provides', 'are', 'all', 'naturally', 'derived', 'this', 'moisturizer', 'contains', 'witch', 'hazel', 'which', 'is', 'an', 'excellent', 'natural', 'source', 'of', 'salicylic', 'acid', 'the', 'juniper', 'cleanses', 'and', 'tones', 'while', 'i', 'hydrate', 'my', 'skin', 'and', 'the', 'included', 'vitamin', 'c', 'repairs', 'sun', 'damage', 'beautifully', 'br', 'br', 'my', 'skin', 'can', 'be', 'very', 'dry', 'especially', 'after', 'cleansing', 'i', 'was', 'very', 'pleased', 'to', 'find', 'that', 'this',

['this', 'is', 'not', 'for', 'oily', 'combination', 'skin', 'because', 'whenever', 'i', 'use', 'it', 'it', 'gave', 'me', 'pimples', 'on', 'my', 'face', 'but', 'i', 'really', 'like', 'their', 'other', 'body', 'cream', 'product', '']
['did', 'not', 'receive', 'correct', 'color', 'ordered', 'blonde', 'received', 'dark', 'brown', '']
['to', 'use', 'the', 'words', 'from', 'wellnesscent', 'there', 'are', 'lots', 'of', 'types', 'of', 'frankincense', 'oil', 'maybe', 'you', 'are', 'used', 'to', 'boswellia', 'carteri', 'or', 'maybe', 'a', 'mix', 'like', 'some', 'brands', 'sell', 'this', 'oil', 'is', 'pure', 'boswellia', 'serrata', 'i', 'did', 'not', 'realize', 'this', 'distinction', 'and', 'was', 'surprised', 'by', 'the', 'scent', 'of', 'the', 'oil', 'because', 'it', 'was', 'not', 'the', 'same', 'as', 'the', 'one', 'i', 'just', 'emptied', 'after', 'contacting', 'the', 'company', 'they', 'gave', 'me', 'a', 'full', 'refund', 'with', 'less', 'than', 'a', 'day', 'i', 'am', 'soooo', 'impressed', 'wit

['very', 'efective', 'gives', 'a', 'great', 'feel', 'to', 'the', 'face', '']
['no', 'comment']
['recently', 'purchased', 'based', 'upon', 'the', 'reviews', 'and', 'used', 'the', 'entire', 'bottle', 'as', 'directed', 'with', 'absolutely', 'zero', 'results', '']
['when', 'you', 'bend', 'your', 'fingers', 'the', 'cover', 'does', 'not', 'bend', 'with', 'them', 'leaving', 'them', 'exposed', '']
['works', 'exactly', 'as', 'advertised', 'being', 'able', 'to', 'rinse', 'it', 'out', 'is', 'really', 'helpful', '']
['you', 'have', 'to', 'use', 'multiple', 'coats', 'to', 'get', 'the', 'coverage', 'plus', 'when', 'you', 'put', 'it', 'on', 'your', 'bottom', 'lashes', 'it', 'smears', 'under', 'your', 'eye', 'so', 'you', 'have', 'to', 'constantly', 'check', 'and', 'recheck', 'for', 'black', 'smears', '']
['nice', 'smell']
['too', 'small', 'from', 'my', 'expectations', '']
['great', 'stuff', 'but', 'from', 'walmart', 'it', 'is', 'way', 'cheaper', '']
['a', 'mouthwash', 'that', 'really', 'helps', 'dry',

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['smells', 'like', 'generic', 'unscented', 'soap', 'not', 'like', 'something', 'good', 'in', 'that', 'category', 'like', 'method', 's', 'sweet', 'water', 'without', 'even', 'a', 'trace', 'of', 'clover', 'or', 'anything', 'fresh', 'in', 'it', '']
['very', 'cute', 'and', 'such', 'a', 'good', 'price', '']
['overall', 'a', 'decent', 'companion', 'to', 'my', 'mua', 'kit', 'the', 'vinyl', 'not', 'leather', 'case', 'is', 'cheap', 'the', 'ties', 'quickly', 'fell', 'apart', 'i', 'purchased', 'two', 'one', 'to', 'keep', 'one', 'to', 'give', '']
['i', 'hate', 'it', 'actually', 'when', 'i', 'got', 'the', 'item', 'it', 'is', 'alreayd', 'over', 'the', 'expiration', 'date', 'i', 'e', 'feb', 'i', 'wonder', 'why', 'you', 'do', 'busines', 'in', 'this', 'manner', 'br', 'br', 'yes', 'it', 'is', 'a', 'cheap', 'but', 'do', 'not', 'think', 'you', 'can', 'cheat', 'the', 'client', 'br', 'br', 'i', 'do', 'expect', 'your', 'appology', 'and', 'comments', 'how', 'you', 'will', 'manage', 'such', 'a', 'case', 'in',

['i', 'have', 'always', 'had', 'a', 'problem', 'with', 'moisturizers', 'for', 'my', 'face', 'because', 'sometimes', 'it', 'is', 'sensitive', 'and', 'other', 'times', 'very', 'sensitive', 'i', 'have', 'found', 'with', 'bio', 'oil', 'it', 'absorbs', 'easily', 'and', 'does', 'not', 'leave', 'a', 'greasy', 'trail', 'and', 'is', 'good', 'for', 'my', 'face', 'and', 'neck', '']
['overall', 'a', 'little', 'disappointed', 'i', 'have', 'only', 'used', 'this', 'for', 'about', 'three', 'weeks', 'and', 'the', 'bottle', 'is', 'nearly', 'empty', 'i', 'feel', 'as', 'if', 'i', 'purchased', 'a', 'bottle', 'of', 'air', 'i', 'definitely', 'would', 'not', 'purchase', 'this', 'product', 'again', '']
['i', 'just', 'rec', 'd', 'my', 'bottle', 'and', 'love', 'love', 'love', 'it', 'br', 'br', 'i', 'have', 'just', 'ordered', 'three', 'bottle', 'of', 't', 'mugler', 'sprays', 'br', 'br', 'thanks']
['i', 'had', 'a', 'wierd', 'arm', 'tan', 'from', 'a', 't', 'shirt', 'and', 'needed', 'to', 'wear', 'a', 'halter', 'dre

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

